# Raw data parsing 

For each experiment, this notebook parses raw, non-anonymized datafiles of individual subjects into one anonymous CSV file.

For Experiment 3, this notebook additionally constructs a .pickle file for model fitting.

The original authors have deleted the raw datafiles to ensure anonymity. Hence, this notebook cannot be run unless you have collected new data and stored the anonymized individual datafiles in the paths below.

In [1]:
import numpy as np
import scipy 
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import random
import os
import pickle
import glob 
import timeit

from matplotlib import colors
divnorm = colors.TwoSlopeNorm(vmin=-0.7, vcenter=0, vmax=0.7)
divnorm_prob = colors.TwoSlopeNorm(vmin=0, vcenter=0.5, vmax=1)

from sklearn.metrics import roc_auc_score

import json
import pandas
from collections import Counter


figpath = os.path.join("fig")
data_savepath = os.path.join("data")

# Experiment 1

In [32]:
datapath = os.path.join("..","experiment","data", "exp1")
T_ends = np.array([3,5,8])

In [33]:
# Parse datafiles

csv_files = glob.glob(os.path.join(datapath, "*.csv"))
n_subj = len(csv_files)
n_questions = len(T_ends)
print(n_subj)
print(T_ends)
print()

choices = np.zeros((n_subj,n_questions))
# mturk_IDs = []
bonus = np.zeros((n_subj))
genders = []
ages = []
comments = []
for subj in range(n_subj): 
#     mturk_ID = csv_files[subj].split("\\")[-1][:-4]
#     print(mturk_ID)
    # read the csv file 
    df_subj = pd.read_csv(csv_files[subj]) 
    subj_T_ends = df_subj["time_horizon"].to_numpy()
    subj_T_ends = subj_T_ends[~np.isnan(subj_T_ends)]
    subj_choice = df_subj["choice"].to_numpy()
    subj_choice = 1-(subj_choice[~np.isnan(subj_choice)]-1)   
    for question in range(n_questions):
        trial_idx = np.where(subj_T_ends==T_ends[question])[0]
        #print(trial_idx)
        choices[subj,question] = np.squeeze(subj_choice[trial_idx]) # Velocity agent is 0, Exploitation agent is 1.
    # mturk_IDs.append(mturk_ID)
    bonus[subj] = np.nansum(df_subj["bonus"].to_numpy())
    
    # Record demographic info of particiapnts
    data_age = json.loads(df_subj["response"].to_numpy()[-3])
    data_gender = json.loads(df_subj["response"].to_numpy()[-2])
    data_comments = json.loads(df_subj["response"].to_numpy()[-1])
    ages.append(int(data_age["Q0"]))
    genders.append(data_gender["Q0"])
    comments.append(data_comments["Q0"])
    
    
choices_mean = np.mean(choices, axis=0) # Velocity agent is 0, Exploitation agent is 1.
choices_std = np.std(choices, ddof=1, axis=0) # Use sample std: denom is (N-1)
choices_sem = choices_std/np.sqrt(n_subj)

letter_counts = Counter(genders)
df_gender = pandas.DataFrame.from_dict(letter_counts, orient='index')
print(df_gender)

# Save experiment data
exp1_data = np.column_stack((np.repeat(np.array(range(n_subj)),n_questions), np.tile([0,1,2],n_subj), np.tile(T_ends,n_subj), choices.flatten().astype(int), np.repeat(np.array(ages),n_questions), np.repeat(np.array(genders),n_questions), np.repeat(np.array(comments),n_questions)))
exp1_df = pd.DataFrame(exp1_data, columns=["SubjectID","Trial","T_end","chooseVelocity","Age","Gender","Comments"])
print()
print(exp1_df)
filename = os.path.join(data_savepath,"exp1_data_df.csv")
exp1_df.to_csv(filename, index=False)

100
[3 5 8]

             0
F           46
M           53
Non-binary   1

    SubjectID Trial T_end chooseVelocity Age Gender  \
0           0     0     3              0  37      F   
1           0     1     5              0  37      F   
2           0     2     8              0  37      F   
3           1     0     3              0  44      F   
4           1     1     5              1  44      F   
..        ...   ...   ...            ...  ..    ...   
295        98     1     5              0  37      F   
296        98     2     8              1  37      F   
297        99     0     3              0  47      F   
298        99     1     5              1  47      F   
299        99     2     8              1  47      F   

                                              Comments  
0    I was asked to decide on a defense against an ...  
1    I was asked to decide on a defense against an ...  
2    I was asked to decide on a defense against an ...  
3    I had to choose which defense sy

# Experiment 2

In [35]:
datapath = os.path.join("..","experiment","data", "exp2")
dataset_name = "exp2"
agent_names = ["velocity", "exploitation"]
t_nows = [2,2,2]
T_ends = [3,5,8]

In [36]:
# Read participant comments
n_questions = len(T_ends)
n_subjs = np.zeros((2,1))


# Total number of subjects that did either condition
datapath = os.path.join("..","experiment","data", dataset_name)
csv_files = glob.glob(os.path.join(datapath, "*.csv"))
n_subj_bothconds = len(csv_files)
# mturk_IDs = []
bonus = np.zeros((n_subj_bothconds))
genders_allconds = {}
ages_allconds = {}
comments_allconds = {}

forced_start_agent_is_exploitation = np.zeros((n_subj_bothconds,)).astype(bool);
responses_allcond = {}
# Obtain which subject did which condition.
for start_agent in range(2):
    # Read CSV files.
    n_subj_inthiscondition = 0;
    for subj in range(n_subj_bothconds): 
#         mturk_ID = csv_files[subj].split("\\")[-1][:-4]
#         if(start_agent==0):
#             mturk_IDs.append(mturk_ID)
        df_subj = pd.read_csv(csv_files[subj]) 
        bonus[subj] = np.nansum(df_subj["bonus"].to_numpy())
        
        subj_assigned_condition = df_subj["forced_start_agent_is_exploitation"][1]
        forced_start_agent_is_exploitation[subj] = subj_assigned_condition
        
        if(subj_assigned_condition==bool(start_agent)):
            n_subj_inthiscondition = n_subj_inthiscondition+1;
    n_subjs[start_agent] = int(n_subj_inthiscondition)
    
            
            
# Store proportion of stay decisions for each condition.
for start_agent in range(2):
    # Read CSV files.
    responses = np.zeros((int(n_subjs[start_agent]),n_questions+1))
    subj_cond = -1;
    genders = []
    ages = []
    comments = []
    for subj in range(n_subj_bothconds): 
        if(start_agent!=bool(forced_start_agent_is_exploitation[subj])): # Subject did the other condition
            continue;
        else:
            subj_cond = subj_cond+1
            
        df_subj = pd.read_csv(csv_files[subj]) 

        subj_response = df_subj["response"].to_numpy()
        # Record demographic info of particiapnts
        data_age = json.loads(df_subj["response"].to_numpy()[-7])
        data_gender = json.loads(df_subj["response"].to_numpy()[-6])
        data_comments = json.loads(df_subj["response"].to_numpy()[-4])
        ages.append(int(data_age["Q0"]))
        genders.append(data_gender["Q0"])
        comments.append(data_comments["Q0"])
    ages_allconds[agent_names[start_agent]] = ages
    genders_allconds[agent_names[start_agent]] = genders
    comments_allconds[agent_names[start_agent]] = comments

    letter_counts = Counter(genders)
    df_gender = pandas.DataFrame.from_dict(letter_counts, orient='index')
    print(df_gender)
    print("\n ------------ \n")
    #responses_allcond[agent_names[start_agent]] = responses

C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3090331119.py:41: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  responses = np.zeros((int(n_subjs[start_agent]),n_questions+1))


                    0
F                  55
M                  43
Non-binary          1
Prefer not to say   1

 ------------ 



C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3090331119.py:41: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  responses = np.zeros((int(n_subjs[start_agent]),n_questions+1))


                    0
F                  48
M                  50
Prefer not to say   2

 ------------ 



In [37]:
choices_mean = np.zeros((2, n_questions))
choices_std = np.zeros((2, n_questions))
choices_sem = np.zeros((2, n_questions))
choices_allconds = {}
testtrajidx_allconds = {}

# Total number of subjects that did either condition
datapath = os.path.join("..","experiment","data", dataset_name)
csv_files = glob.glob(os.path.join(datapath, "*.csv"))
n_subj_bothconds = len(csv_files)
mturk_IDs = []
bonus = np.zeros((n_subj_bothconds))
forced_start_agent_is_exploitation = np.zeros((n_subj_bothconds,)).astype(bool);

# Obtain which subject did which condition.
for start_agent in range(2):
    # Read CSV files.
    n_subj_inthiscondition = 0;
    for subj in range(n_subj_bothconds): 
        mturk_ID = csv_files[subj].split("\\")[-1][:-4]
        if(start_agent==0):
            mturk_IDs.append(mturk_ID)
        df_subj = pd.read_csv(csv_files[subj]) 
        bonus[subj] = np.nansum(df_subj["bonus"].to_numpy())
        
        subj_assigned_condition = df_subj["forced_start_agent_is_exploitation"][1]
        forced_start_agent_is_exploitation[subj] = subj_assigned_condition
        
        if(subj_assigned_condition==bool(start_agent)):
            n_subj_inthiscondition = n_subj_inthiscondition+1;
    n_subjs[start_agent] = int(n_subj_inthiscondition)
    
# Save bonus information
d = {'ID': mturk_IDs, 'bonus': bonus}
df_bonus = pd.DataFrame(data=d)
#df_bonus.to_csv("bonus_exp2.csv", columns=None, header=False, index=False)
print(n_subjs)
print(len(mturk_IDs))
print(forced_start_agent_is_exploitation.shape)
print(len(bonus))         
            
       

[[100.]
 [100.]]
200
(200,)
200


In [38]:
     
            
# Store proportion of stay decisions for each condition.
for start_agent in range(2):
    
    # Read CSV files.
    genders = []
    ages = []
    comments = []
    choices = np.zeros((int(n_subjs[start_agent]),n_questions))
    testtrajidxs = np.zeros((int(n_subjs[start_agent]),))
    subj_cond = -1;
    
    for subj in range(n_subj_bothconds): 
        if(start_agent!=bool(forced_start_agent_is_exploitation[subj])): # Subject did the other condition
            continue;
        else:
            subj_cond = subj_cond+1
            
        df_subj = pd.read_csv(csv_files[subj]) 
        # Record demographic info of particiapnts
        data_age = json.loads(df_subj["response"].to_numpy()[-7])
        data_gender = json.loads(df_subj["response"].to_numpy()[-6])
        data_comments = json.loads(df_subj["response"].to_numpy()[-4])
        ages.append(int(data_age["Q0"]))
        genders.append(data_gender["Q0"])
        comments.append(data_comments["Q0"])
        
        testtrajidxs[subj_cond] = df_subj["test_task_traj_idx"].to_numpy()[-1]
        subj_testorder = df_subj["time_horizon"].to_numpy()
        subj_testorder = subj_testorder[~np.isnan(subj_testorder)].astype(int)
        subj_choice = df_subj["choice"].to_numpy()
        subj_choice = subj_choice[~np.isnan(subj_choice)]
        test_order_idx = np.argsort(subj_testorder)
        for trial in range(len(T_ends)):
            choices[subj_cond,trial] = subj_choice[test_order_idx[trial]]

    # Save experiment data
    n_subj_cond = int(n_subjs[start_agent])          
    exp2_data = np.column_stack((np.tile([agent_names[start_agent]],n_subj_cond*n_questions), np.repeat(np.array(range(n_subj_cond)),n_questions), np.tile(range(n_questions),n_subj_cond), np.tile(t_nows,n_subj_cond), np.tile(T_ends,n_subj_cond), np.repeat(testtrajidxs,n_questions).astype(int), choices.flatten().astype(int), np.repeat(np.array(ages),n_questions), np.repeat(np.array(genders),n_questions), np.repeat(np.array(comments),n_questions)))
    exp2_df_temp = pd.DataFrame(exp2_data, columns=["startAgent","SubjectID","Trial","t_now","T_end","testTrajIdx","chooseSwitch","Age","Gender","Comments"])
    if(start_agent==0):
        exp2_df = exp2_df_temp
    else:
        exp2_df = pd.concat([exp2_df, exp2_df_temp])
    print()
    print(exp2_df)
    
    
filename = os.path.join(data_savepath,"exp2_data_df.csv")
exp2_df.to_csv(filename, index=False)

C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3226552828.py:8: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  choices = np.zeros((int(n_subjs[start_agent]),n_questions))
C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3226552828.py:9: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  testtrajidxs = np.zeros((int(n_subjs[start_agent]),))
C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3226552828.py:37: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  n_subj_cond = i


    startAgent SubjectID Trial t_now T_end testTrajIdx chooseSwitch Age  \
0     velocity         0     0     2     3           1            1  51   
1     velocity         0     1     2     5           1            0  51   
2     velocity         0     2     2     8           1            0  51   
3     velocity         1     0     2     3           2            1  46   
4     velocity         1     1     2     5           2            1  46   
..         ...       ...   ...   ...   ...         ...          ...  ..   
295   velocity        98     1     2     5           0            0  60   
296   velocity        98     2     2     8           0            0  60   
297   velocity        99     0     2     3           1            1  28   
298   velocity        99     1     2     5           1            0  28   
299   velocity        99     2     2     8           1            0  28   

    Gender                                           Comments  
0        F  I recalled which one s

C:\Users\liu_s\AppData\Local\Temp\ipykernel_43036\3226552828.py:37: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  n_subj_cond = int(n_subjs[start_agent])


# Experiment 3

In [2]:
datapath = os.path.join("..","experiment","data", "exp3")

In [3]:
# Compute bonus
csv_files = glob.glob(os.path.join(datapath, "*.csv"))
n_subj = len(csv_files)
bonus = np.zeros((n_subj))
# mturk_IDs = []
feedbacks = []
for subj in range(n_subj): 
    # Bonus info
#     mturk_ID = csv_files[subj].split("\\")[-1][:-4]
#     mturk_IDs.append(mturk_ID)
    #print(mturk_ID)
    df_subj = pd.read_csv(csv_files[subj])
    #print(df_subj["total_bonus"].to_numpy()[-1])
    bonus[subj] = df_subj["total_bonus"].to_numpy()[-1]
    feedbacks.append(df_subj["response"].to_numpy()[-1])
    #print(df_subj["response"].to_numpy()[-1])
# # Grant bonus
# d = {'ID': mturk_IDs, 'bonus': bonus}
# df_bonus = pd.DataFrame(data=d)
# df_bonus.to_csv("bonus_exp3.csv", columns=None, header=False, index=False)


# Convert to CSV

In [20]:
(df_subj_cond['trial_idx']==run) & (df_subj_cond['is_practice']==1)

39     False
40     False
41     False
42     False
43     False
       ...  
749    False
750    False
751    False
752    False
753    False
Length: 605, dtype: bool

In [44]:
# Parse data
T_end = 10
n_conds = 2
n_runs = 50
n_practice_runs = 5
n_timesteps = 10 # Month 0 to 9 -- Month 10 has no response, while Month 0 does not offer evidence and cannot switch.
data = np.zeros((n_conds, n_subj, n_runs, n_timesteps, 2)) # [cond, subj, run_idx, timestep (Month 0 to 9 inclusive), current traj height, decision]
data[:] = np.nan
traj_heights = np.zeros((n_conds,n_subj,n_runs,n_timesteps,2)) #[cond,subj,run_idx, timestep(Month 0 to 9 inclusive)]
starting_traj_heights_counterfactual = np.zeros((n_conds,n_subj,n_runs,n_timesteps))  # traj height if subject stayed till the end; [cond,subj,run_idx, timestep(Month 0 to 9 inclusive)]
traj_params = np.zeros((n_conds, n_subj, n_runs, 2)) # 2 is for the current traj and the new traj if switched. 
cond_names = ["separate-late","separate-early"]

genders = []
ages = []
comments = []

for subj in range(n_subj): 
    
    df_subj = pd.read_csv(csv_files[subj])
    
    # Record demographic info of particiapnts
    data_age = json.loads(df_subj["response"].to_numpy()[-4])
    data_gender = json.loads(df_subj["response"].to_numpy()[-3])
    data_comments = json.loads(df_subj["response"].to_numpy()[-1])
    ages.append(int(data_age["Q0"]))
    genders.append(data_gender["Q0"])
    comments.append(data_comments["Q0"])
    
    # Extract meaningful data
    first_cond_issepearly = df_subj.iloc[0,6]
    print(subj,first_cond_issepearly)
    df_subj = df_subj.iloc[:,20:-2].dropna() # Remove raw data columns
    #df_subj = df_subj.drop(df_subj[df_subj['is_practice']>0].index) # Remove training block 2
    #df_subj = df_subj.drop(df_subj[df_subj['t_now']==T_end].index) # Remove timept t=T_end, because subjects cannot respond
    
    # Define Cond 0 as the "separate late" condition.
    if(first_cond_issepearly):
        df_subj['cond'] = df_subj['cond'].replace(0, cond_names[1])
        df_subj['cond'] = df_subj['cond'].replace(1, cond_names[0])
        cond_iter = [1,0]
    else:
        df_subj['cond'] = df_subj['cond'].replace(0, cond_names[0])
        df_subj['cond'] = df_subj['cond'].replace(1, cond_names[1])
        cond_iter = [0,1]
    df_subj["SubjectID"] = subj
    df_subj["first_cond_issepearly"] = first_cond_issepearly
    df_subj["Age"] = int(data_age["Q0"])
    df_subj["Gender"] = data_gender["Q0"]
    df_subj["Comments"] = data_comments["Q0"]
    
    cols = list(df_subj)
    # move the column to head of list using index, pop and insert
    cols.insert(0, cols.pop(cols.index('SubjectID')))
    cols.insert(1, cols.pop(cols.index('cond')))
    cols.insert(2, cols.pop(cols.index('is_practice')))
    df_subj = df_subj.loc[:, cols]
    
    subject_cum_runcount = -1
    for cond in cond_iter:
        df_subj_cond = df_subj[df_subj['cond']==cond_names[cond]] # Get all data in this task condition.
        for practice_run in range(n_practice_runs):
            subject_cum_runcount = subject_cum_runcount+1
            df_subj_cond_run = df_subj_cond[(df_subj_cond['trial_idx']==practice_run) & (df_subj_cond['is_practice']==1)] # Get all data in this run.
            df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
            if(subj==0 and cond==0 and practice_run==0):
                exp3_data_df = df_subj_cond_run
            else:
                exp3_data_df = pd.concat([exp3_data_df,df_subj_cond_run])
        for run in range(n_runs):
            subject_cum_runcount = subject_cum_runcount+1
            df_subj_cond_run = df_subj_cond[(df_subj_cond['trial_idx']==run) & (df_subj_cond['is_practice']==0)] # Get all data in this run.
            df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
            exp3_data_df = pd.concat([exp3_data_df,df_subj_cond_run])
    
cols = list(exp3_data_df)
cols.insert(1, cols.pop(cols.index('subject_cumulative_trial_idx')))
exp3_data_df = exp3_data_df.loc[:, cols]
            

#             traj_params[cond,subj,run,0] = df_subj_cond_run['start_traj_theta'].to_numpy()[0]
#             traj_params[cond,subj,run,1] = df_subj_cond_run['switch_traj_theta'].to_numpy()[0]
#             for t in range(n_timesteps):
#                 if(has_switched[t]!=1): # Has not switched yet -- hence can still make decision
#                     data[cond, subj, run, t, 0] = start_traj_height[t] # This is the height of the starting traj observed, before subject made the current decision.
#                     if(t>0): # Cannot make decisions at Month 0.
#                         data[cond, subj, run, t, 1] = 1-switched_now[t].astype(int) # 0 is switch, 1 is stay

# letter_counts = Counter(genders)
# df_gender = pandas.DataFrame.from_dict(letter_counts, orient='index')
# print(df_gender)

#print(exp3_data_df)

0 0


C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

1 1


C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

...

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount
C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of 

C:\Users\liu_s\AppData\Local\Temp\ipykernel_26968\95755133.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_subj_cond_run.loc[:,"subject_cumulative_trial_idx"] = subject_cum_runcount


In [45]:
exp3_data_df

SubjectID  subject_cumulative_trial_idx            cond  is_practice  \
20            0                             0   separate-late          1.0   
21            0                             0   separate-late          1.0   
22            0                             0   separate-late          1.0   
23            0                             0   separate-late          1.0   
24            0                             0   separate-late          1.0   
...         ...                           ...             ...          ...   
1468         79                           109  separate-early          0.0   
1469         79                           109  separate-early          0.0   
1470         79                           109  separate-early          0.0   
1471         79                           109  separate-early          0.0   
1472         79                           109  separate-early          0.0   

      trial_idx  t_now  T_end  switched_now  has_switched  t_start_traj  \
20          0.0    0.0   10.0           0.0           0.0           0.0   
21          0.0    1.0   10.0           0.0           0.0           1.0   
22          0.0    2.0   10.0           0.0           0.0           2.0   
23          0.0    3.0   10.0           0.0           0.0           3.0   
24          0.0    4.0   10.0           0.0           0.0           4.0   
...         ...    ...    ...           ...           ...           ...   
1468       49.0    6.0   10.0           0.0           1.0           4.0   
1469       49.0    7.0   10.0           0.0           1.0           4.0   
1470       49.0    8.0   10.0           0.0           1.0           4.0   
1471       49.0    9.0   10.0           0.0           1.0           4.0   
1472       49.0   10.0   10.0           0.0           1.0           4.0   

      t_switch_traj  start_traj_height  switch_traj_height  start_traj_theta  \
20              0.0       0.000000e+00            0.000000          0.497795   
21              0.0       8.807415e-07            0.000000          0.497795   
22              0.0       1.307896e-05            0.000000          0.497795   
23              0.0       1.819667e-04            0.000000          0.497795   
24              0.0       2.509383e-03            0.000000          0.497795   
...             ...                ...                 ...               ...   
1468            2.0       3.832472e-01            0.328008          0.388455   
1469            3.0       3.832486e-01            0.730937          0.388455   
1470            4.0       3.832487e-01            0.871228          0.388455   
1471            5.0       3.832487e-01            0.894070          0.388455   
1472            6.0       3.832487e-01            0.897207          0.388455   

      switch_traj_theta  first_cond_issepearly  Age Gender  \
20             0.545024                      0   41      M   
21             0.545024                      0   41      M   
22             0.545024                      0   41      M   
23             0.545024                      0   41      M   
24             0.545024                      0   41      M   
...                 ...                    ...  ...    ...   
1468           0.907158                      0   48      F   
1469           0.907158                      0   48      F   
1470           0.907158                      0   48      F   
1471           0.907158                      0   48      F   
1472           0.907158                      0   48      F   

                                               Comments  
20    If there wasn't good progress by month 4 then ...  
21    If there wasn't good progress by month 4 then ...  
22    If there wasn't good progress by month 4 then ...  
23    If there wasn't good progress by month 4 then ...  
24    If there wasn't good progress by month 4 then ...  
...                                                 ...  
1468  I based my decisions on how I was progressing ... 

In [46]:
filename = os.path.join(data_savepath,"exp3_data_df.csv")
exp3_data_df.to_csv(filename, index=False)

# Convert to .pickle

In [47]:
filename = os.path.join(data_savepath,"exp3_data_df.csv")
exp3_data_df = pd.read_csv(filename)

In [48]:
# Parse data
T_end = 10
n_conds = 2
n_runs = 50
n_timesteps = 10 # Month 0 to 9 -- Month 10 has no response, while Month 0 does not offer evidence and cannot switch.
data = np.zeros((n_conds, n_subj, n_runs, n_timesteps, 2)) # [cond, subj, run_idx, timestep (Month 0 to 9 inclusive), current traj height, decision]
data[:] = np.nan
traj_heights = np.zeros((n_conds,n_subj,n_runs,n_timesteps,2)) #[cond,subj,run_idx, timestep(Month 0 to 9 inclusive)]
starting_traj_heights_counterfactual = np.zeros((n_conds,n_subj,n_runs,n_timesteps))  # traj height if subject stayed till the end; [cond,subj,run_idx, timestep(Month 0 to 9 inclusive)]
traj_params = np.zeros((n_conds, n_subj, n_runs, 2)) # 2 is for the current traj and the new traj if switched. 


genders = []
ages = []
comments = []



for subj in range(n_subj): 
    print(subj)
    
    df_subj = exp3_data_df[exp3_data_df["SubjectID"]==subj]
    df_subj = df_subj.drop(df_subj[df_subj['is_practice']>0].index) # Remove training block 2
    df_subj = df_subj.drop(df_subj[df_subj['t_now']==T_end].index) # Remove timept t=T_end, because subjects cannot respond

    
    # Record demographic info of particiapnts
    ages.append(int(df_subj.iloc[0,:]["Age"]))
    genders.append(df_subj.iloc[0,:]["Gender"])
    comments.append(df_subj.iloc[0,:]["Comments"])
    
    # Extract meaningful data
    first_cond_issepearly = int(df_subj.iloc[0,:]["first_cond_issepearly"])

    # Define Cond 0 as the "separate late" condition
    for cond in range(n_conds):
        df_subj_cond = df_subj[df_subj['cond']==cond_names[cond]] # Get all data in this task condition.
        for run in range(n_runs):
            df_subj_cond_run = df_subj_cond[df_subj_cond['trial_idx']==run] # Get all data in this run.
            has_switched = df_subj_cond_run['has_switched'].to_numpy()
            switched_now = df_subj_cond_run['switched_now'].to_numpy()
            start_traj_height = df_subj_cond_run['start_traj_height'].to_numpy()
            starting_traj_heights_counterfactual[cond,subj,run,:] = start_traj_height
            switch_traj_height = df_subj_cond_run['switch_traj_height'].to_numpy()
            traj_params[cond,subj,run,0] = df_subj_cond_run['start_traj_theta'].to_numpy()[0]
            traj_params[cond,subj,run,1] = df_subj_cond_run['switch_traj_theta'].to_numpy()[0]
            for t in range(n_timesteps):
                if(has_switched[t]!=1): # Has not switched yet -- hence can still make decision
                    data[cond, subj, run, t, 0] = start_traj_height[t] # This is the height of the starting traj observed, before subject made the current decision.
                    if(t>0): # Cannot make decisions at Month 0.
                        data[cond, subj, run, t, 1] = 1-switched_now[t].astype(int) # 0 is switch, 1 is stay

letter_counts = Counter(genders)
df_gender = pandas.DataFrame.from_dict(letter_counts, orient='index')
print(df_gender)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
             0
M           43
F           36
Non-binary   1


In [49]:
# Get trajectory heights at T_end=10.
traj_finalheights = np.zeros((n_conds,n_subj,n_runs,2)) #[cond,subj,run_idx, timestep(Month 0 to 1- inclusive)]
for subj in range(n_subj): 
    df_subj = exp3_data_df[exp3_data_df["SubjectID"]==subj]
    df_subj = df_subj.drop(df_subj[df_subj['is_practice']>0].index) # Remove training block 2
    df_subj_Tend = df_subj[df_subj['t_now']==T_end].copy() # Remove timept t=T_end, because subjects cannot respond

    # Extract meaningful data
    first_cond_issepearly = int(df_subj.iloc[0,:]["first_cond_issepearly"])
    for cond in range(n_conds):
        df_subj_cond_Tend = df_subj_Tend[df_subj_Tend['cond']==cond_names[cond]] # Get all data in this task condition.
        traj_finalheights[cond,subj,:,0] = df_subj_cond_Tend['start_traj_height']
        traj_finalheights[cond,subj,:,1] = df_subj_cond_Tend['switch_traj_height']

In [50]:
# Create exp3_data.pickle, which is needed for model fits

filename = os.path.join(data_savepath,"exp3_data")
a = {"mturk_IDs":[], 'data_dims': ["condition (0 is separate late)","subject","run","timestep (Month 0 to 9)","data (current trajectory height, current decision)"], 'data': data, 'traj_params':traj_params, "counterfactual_traj_finalheights": traj_finalheights, "starting_traj_heights_counterfactual":starting_traj_heights_counterfactual, "ages":ages,"genders":genders,"comments":comments}
with open(filename+'.pickle', 'wb') as handle:
    pickle.dump(a, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open(filename+".pickle", 'rb') as handle:
    b = pickle.load(handle)
print(b.keys())

dict_keys(['mturk_IDs', 'data_dims', 'data', 'traj_params', 'counterfactual_traj_finalheights', 'starting_traj_heights_counterfactual', 'ages', 'genders', 'comments'])
